In [ ]:
# Install required packages
!pip install transformers datasets torch pandas scikit-learn wandb
!pip install transformers[torch] accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 12.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 67.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 MB 15.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 15.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 15.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 14.4 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.

In [ ]:
from datasets import load_dataset
from transformers import RobertaTokenizer, RobertaForSequenceClassification, Trainer, TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
import torch
import numpy as np
import wandb
from huggingface_hub import HfApi, Repository
import os
import shutil

In [ ]:
# Initialize wandb
wandb.init(project="tos-roberta-classifier", name="roberta-large-run")

# Load the dataset
dataset = load_dataset('CodeHima/TOS_Dataset')

Generating train split:   0%|          | 0/5378 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/415 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1038 [00:00<?, ? examples/s]

In [ ]:
# Initialize the tokenizer
tokenizer = RobertaTokenizer.from_pretrained('roberta-large')

# Create label mapping
label_mapping = {'clearly_fair': 0, 'potentially_unfair': 1, 'clearly_unfair': 2}

def tokenize_and_encode(examples):
    tokenized = tokenizer(examples['sentence'], padding='max_length', truncation=True, max_length=512)
    tokenized['labels'] = [label_mapping[label] for label in examples['unfairness_level']]
    return tokenized

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

In [ ]:
# Tokenize and encode the dataset
tokenized_dataset = dataset.map(tokenize_and_encode, batched=True, remove_columns=dataset['train'].column_names)

# Set the format for PyTorch
tokenized_dataset.set_format(type='torch', columns=['input_ids', 'attention_mask', 'labels'])

Map:   0%|          | 0/5378 [00:00<?, ? examples/s]

Map:   0%|          | 0/415 [00:00<?, ? examples/s]

Map:   0%|          | 0/1038 [00:00<?, ? examples/s]

In [ ]:
# Split the dataset
train_data = tokenized_dataset['train']
validation_data = tokenized_dataset['validation']
test_data = tokenized_dataset['test']

In [ ]:
# Load the model
num_labels = 3  # clearly_fair, potentially_unfair, clearly_unfair
model = RobertaForSequenceClassification.from_pretrained('roberta-large', num_labels=num_labels)

# Define training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=5,  # Increased from 3 to 5
    per_device_train_batch_size=8,  # Reduced from 16 to 8 due to larger model
    per_device_eval_batch_size=8,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    metric_for_best_model="eval_f1",
    report_to="wandb",  # Report to wandb
    learning_rate=2e-5,  # Slightly lower learning rate
    fp16=True,  # Use mixed precision training
)

# Define the compute metrics function
def compute_metrics(pred):
    labels = pred.label_ids
    preds = np.argmax(pred.predictions, axis=-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall
    }

# Initialize the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=validation_data,
    compute_metrics=compute_metrics
)

model.safetensors:   0%|          | 0.00/1.42G [00:00<?, ?B/s]

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-large and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1494: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
# Train the model
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


TrainOutput(global_step=3365, training_loss=0.3287806587534532, metrics={'train_runtime': 3310.0901, 'train_samples_per_second': 8.124, 'train_steps_per_second': 1.017, 'total_flos': 2.505971903112192e+16, 'train_loss': 0.3287806587534532, 'epoch': 5.0})

In [ ]:
# Evaluate the model on validation data
validation_results = trainer.evaluate(eval_dataset=validation_data)
print(f"Validation Accuracy: {validation_results['eval_accuracy']}")

# Evaluate the model on test data
test_results = trainer.evaluate(eval_dataset=test_data)
print(f"Test Accuracy: {test_results['eval_accuracy']}")

# Save the model
model.save_pretrained('./tos-roberta-classifier')
tokenizer.save_pretrained('./tos-roberta-classifier')

Validation Accuracy: 0.8963855421686747
Test Accuracy: 0.8583815028901735


('./tos-roberta-classifier/tokenizer_config.json',
 './tos-roberta-classifier/special_tokens_map.json',
 './tos-roberta-classifier/vocab.json',
 './tos-roberta-classifier/merges.txt',
 './tos-roberta-classifier/added_tokens.json')

In [ ]:
# Function to predict unfairness level
def predict_unfairness(text, model, tokenizer):
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True, max_length=512)

    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)

    probabilities = torch.softmax(outputs.logits, dim=-1).squeeze()
    predicted_class = torch.argmax(probabilities).item()

    inverse_label_mapping = {0: 'clearly_fair', 1: 'potentially_unfair', 2: 'clearly_unfair'}
    predicted_label = inverse_label_mapping[predicted_class]

    return predicted_label, probabilities.tolist()

In [ ]:
# Test the model
def test_model():
    model_path = './tos-roberta-classifier'
    model = RobertaForSequenceClassification.from_pretrained(model_path)
    tokenizer = RobertaTokenizer.from_pretrained(model_path)

    while True:
        text = input("Enter a clause to classify (or 'quit' to exit): ")
        if text.lower() == 'quit':
            break

        predicted_label, probabilities = predict_unfairness(text, model, tokenizer)

        print(f"\nPredicted unfairness level: {predicted_label}")
        print("Probabilities:")
        for label, prob in zip(['clearly_fair', 'potentially_unfair', 'clearly_unfair'], probabilities):
            print(f"{label}: {prob:.4f}")
        print()

In [ ]:
if __name__ == "__main__":
    test_model()

Enter a clause to classify (or 'quit' to exit): We reserve the right to suspend, terminate, or restrict your access to the platform at any time and for any reason, without prior notice or explanation. This includes but is not limited to violations of our community guidelines or terms of service, as determined solely by ConnectWorld.

Predicted unfairness level: potentially_unfair
Probabilities:
clearly_fair: 0.0034
potentially_unfair: 0.9077
clearly_unfair: 0.0889

Enter a clause to classify (or 'quit' to exit): We are committed to protecting your privacy and personal information. We will not sell or share your data with third parties without your consent, except as required by law or as necessary to provide our services. Our privacy policy outlines how we collect, use, and protect your data.

Predicted unfairness level: clearly_fair
Probabilities:
clearly_fair: 0.9953
potentially_unfair: 0.0044
clearly_unfair: 0.0002

Enter a clause to classify (or 'quit' to exit):  We reserve the rig

In [ ]:
# Push the model to Hugging Face Hub
def push_to_hub():
    # Set your Hugging Face token and repo name
    hf_token = "Your_HuggingFace_APi"
    repo_name = "Tos-Roberta"

    # Set the path to your local model
    local_model_path = "./tos-roberta-classifier"

    # Initialize Hugging Face API
    api = HfApi()

    # Create a new repository
    repo_url = api.create_repo(
        repo_id=repo_name,
        token=hf_token,
        private=False,
        exist_ok=True
    )

    # Clone the empty repository
    repo = Repository(local_dir=repo_name, clone_from=repo_url, use_auth_token=hf_token)

    # Load your trained model and tokenizer
    model = RobertaForSequenceClassification.from_pretrained(local_model_path)
    tokenizer = RobertaTokenizer.from_pretrained(local_model_path)

    # Save the model and tokenizer to the cloned repository
    model.save_pretrained(repo_name)
    tokenizer.save_pretrained(repo_name)

    # Add a README file
    with open(os.path.join(repo_name, "README.md"), "w") as f:
        f.write("# Tos-Roberta\n\nThis model is trained to classify clauses in Terms of Service (ToS) documents using RoBERTa-large.")

    # Push the files to the Hugging Face Hub
    repo.git_add()
    repo.git_commit("Initial commit")
    repo.git_push()

    print(f"Model successfully pushed to https://huggingface.co/{repo_name}")

In [ ]:
if __name__ == "__main__":
    test_model()
    push_to_hub()

Enter a clause to classify (or 'quit' to exit): quit


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)
Cloning https://huggingface.co/CodeHima/Tos-Roberta into local empty directory.


Upload file model.safetensors:   0%|          | 1.00/1.32G [00:00<?, ?B/s]

remote: -------------------------------------------------------------------------        
remote: Your push was accepted, but with warnings:         
remote: - Warning: empty or missing yaml metadata in repo card        
remote: help: https://huggingface.co/docs/hub/model-cards#model-card-metadata        
remote: -------------------------------------------------------------------------        
remote: -------------------------------------------------------------------------        
remote: Please find the documentation at:        
remote: https://huggingface.co/docs/hub/model-cards#model-card-metadata        
remote:         
remote: -------------------------------------------------------------------------        
To https://huggingface.co/CodeHima/Tos-Roberta
   b7f5bf7..57579c3  main -> main

remote: Your push was accepted, but with warnings:         
remote: - Warning: empty or missing yaml metadata in repo card        
remote: help: https://huggingface.co/docs/hub/model-cards#model

Model successfully pushed to https://huggingface.co/Tos-Roberta


In [ ]:
# Finish wandb run
wandb.finish()